In [ ]:
'''
Assuming the financial_aggregating script has been run, with organisations matched and stored...

Going to use the pickled results and do some filtering, etc. to get to some results

But would like to know what organisations have been checked/found/matched for reference

Date updated: 2022/11/15
'''

In [1]:
import pandas as pd
import numpy as np

import xlsxwriter

from __future__ import unicode_literals
import unittest
import re
import sys


import math

In [3]:
# load pickled matched data
new_oscar = pd.read_pickle('2022_10_17_matched_oscar.pkl')

In [ ]:
# CHECKING MATCHING ROUTINE AREA...

In [2]:
# read in the original oscar file 
oscar = pd.read_csv('Source files\\2021_OSCAR_Extract_2020_21.txt', delimiter='|', encoding='cp1252') # skiprows=12, )
# read in set of organisations being matched against
checked_orgs = pd.read_excel('oscar_organisation_matching_checked.xlsx', sheet_name='2022_09_05')


C:\Users\shepleyp\AppData\Local\Temp\ipykernel_15712\494649564.py:2: DtypeWarning: Columns (23,24,44,72,73) have mixed types. Specify dtype option on import or set low_memory=False.
  oscar = pd.read_csv('Source files\\2021_OSCAR_Extract_2020_21.txt', delimiter='|', encoding='cp1252') # skiprows=12, )


In [16]:
# create lists of matching organisations

# from original oscar dataset
original_oscar_organisation_list = oscar['ORGANISATION_LONG_NAME'].unique()

In [17]:
# from checked_orgs
checked_oscar_organisation_list = checked_orgs['ORGANISATION_LONG_NAME'].unique()
checked_organisation_list = checked_orgs['ONS names'].unique()

# from new_oscar dataset
checked_new_oscar_organisation_list = new_oscar['ORGANISATION_LONG_NAME'].unique()
checked_new_oscar_ifg_name = new_oscar['Checked_Organisation_Name'].unique()
checked_new_oscar_ifg_type = new_oscar['IfG_Organisation_Type'].unique()

In [18]:
# write findings into an excel workbook
with pd.ExcelWriter('organisation_checking_2011_11_15.xlsx') as writer:
    
    original_oscar_df = pd.DataFrame(original_oscar_organisation_list,
                                    columns=['OSCAR NAME'])
    original_oscar_df.to_excel(writer, sheet_name='OriginalOSCAR')
    
    checked_oscar_df = pd.DataFrame(list(zip(checked_oscar_organisation_list, checked_organisation_list)),
                                   columns=['OSCAR NAME', 'ONS name'])
    checked_oscar_df.to_excel(writer, sheet_name='MatchedOSCAR')
    
    new_oscar_df = pd.DataFrame(list(zip(checked_new_oscar_organisation_list, checked_new_oscar_ifg_name, checked_new_oscar_ifg_type)),
                               columns = ['OSCAR NAME', 'Checked (IfG) name', 'IfG type'])
    
    new_oscar_df.to_excel(writer, sheet_name='TypeOSCAR')
    
    writer.save()

In [ ]:
# aggregating financial numbers for checking - want to run a couple of different cuts from OSCAR pickle

In [20]:
# choose cut here

# financial year, final outturns
R13 = new_oscar[new_oscar['VERSION_CODE']=='R13']

In [21]:
# positive values
R13_positive = R13[R13['AMOUNT']>0]

In [ ]:
# exclude NON-BUDGET and NON-VOTED


In [29]:
# use groupby for target categories
groupby_categories = [
    'ORGANISATION_LONG_NAME',
    'Checked_Organisation_Name',
    'IfG_Organisation_Type',
    'ORGANISATION_TYPE_L1_LONG_NAME',
    'PESA_ECONOMIC_BUDGET_CODE',
    'PESA_ECONOMIC_GROUP_CODE',
    'INCOME_CATEGORY_SHORT_NAME',
    'CHART_OF_ACCOUNTS_L5_LONG_NAME',
    'ECONOMIC_BUDGET_CODE',
    'CONTROL_BUDGET_L0_LONG_NAME',
    'ACCOUNTING_AUTHORITY_L0_CODE',
    'ECONOMIC_CATEGORY_LONG_NAME',
    'ECONOMIC_GROUP_LONG_NAME'
]

oscar_grouped = R13_positive.groupby(groupby_categories)['AMOUNT'].sum()

In [30]:
oscar_grouped_df = oscar_grouped.to_frame()

In [32]:
oscar_grouped_df.reset_index(inplace=True)

In [35]:
oscar_grouped_df['AMOUNT'].sum()

2880322535.0

In [36]:
oscar_grouped_df

ORGANISATION_LONG_NAME                  Checked_Organisation_Name  \
0                 Academies                        Academies (En Bloc)   
1                 Academies                        Academies (En Bloc)   
2                 Academies                        Academies (En Bloc)   
3                 Academies                        Academies (En Bloc)   
4                 Academies                        Academies (En Bloc)   
...                     ...                                        ...   
5902    Youth Justice Board  Youth Justice Board for England and Wales   
5903    Youth Justice Board  Youth Justice Board for England and Wales   
5904    Youth Justice Board  Youth Justice Board for England and Wales   
5905    Youth Justice Board  Youth Justice Board for England and Wales   
5906    Youth Justice Board  Youth Justice Board for England and Wales   

     IfG_Organisation_Type ORGANISATION_TYPE_L1_LONG_NAME  \
0                 Devolved               ARMS LENGTH BODY   
1                 Devolved               ARMS LENGTH BODY   
2                 Devolved               ARMS LENGTH BODY   
3                 Devolved               ARMS LENGTH BODY   
4                 Devolved               ARMS LENGTH BODY   
...                    ...                            ...   
5902           Public Body               ARMS LENGTH BODY   
5903           Public Body               ARMS LENGTH BODY   
5904           Public Body               ARMS LENGTH BODY   
5905           Public Body               ARMS LENGTH BODY   
5906           Public Body               ARMS LENGTH BODY   

     PESA_ECONOMIC_BUDGET_CODE                      PESA_ECONOMIC_GROUP_CODE  \
0                      CAPITAL  CAPITAL GRANTS TO PERSONS & NON-PROFIT (NET)   
1                      CAPITAL                   INCOME FROM SALES OF ASSETS   
2                      CAPITAL                                 OTHER CAPITAL   
3                      CAPITAL                            PURCHASE OF ASSETS   
4                      CAPITAL                            PURCHASE OF ASSETS   
...                        ...                                           ...   
5902                  RESOURCE                                   STAFF COSTS   
5903                  RESOURCE                                   STAFF COSTS   
5904                  RESOURCE                                   STAFF COSTS   
5905                  RESOURCE                                   STAFF COSTS   
5906                  RESOURCE                         TAKE UP OF PROVISIONS   

     INCOME_CATEGORY_SHORT_NAME  \
0                  OTHER GRANTS   
1               SALES OF ASSETS   
2                  OTHER GRANTS   
3                         GROSS   
4                         GROSS   
...                         ...   
5902                      GROSS   
5903                      GROSS   
5904                      GROSS   
5905               OTHER INCOME   
5906                      GROSS   

                         CHART_OF_ACCOUNTS_L5_LONG_NAME ECONOMIC_BUDGET_CODE  \
0     INC - CAPITAL GRANTS FROM PRIVATE SECTOR - PER...              CAPITAL   
1            PPE - BUILDINGS (OWNED) - COST - DISPOSALS              CAPITAL   
2          INC - CAPITAL GRANTS FROM CENTRAL GOVERNMENT              CAPITAL   
3            PPE - BUILDINGS (OWNED) - COST - ADDITIONS              CAPITAL   
4            PPE - POA & AUC (OWNED) - COST - DONATIONS              CAPITAL   
...                                                 ...                  ...   
5902  EXP - PERMANENT UK STAFF - EMPLOYER'S SOCIAL S...             RESOURCE   
5903             EXP - SECONDED UK STAFF - BASIC SALARY             RESOURCE   
5904  EXP - SHORT-TERM CONTRACT & AGENCY STAFF - FUL...             RESOURCE   
5905                   INC - RECOVERY OF SECONDEE COSTS             RESOURCE   
5906                   EXP - PROVISIONS EXPENSE - OTHER             RESOURCE   

          CONTROL_BUDGET_L0_LONG_NAME AC

In [38]:
# check organisation list is sustained in these cells below
len(oscar_grouped_df['ORGANISATION_LONG_NAME'].unique())

248

In [39]:
len(R13_positive['ORGANISATION_LONG_NAME'].unique())

250

In [40]:
set(oscar_grouped_df['ORGANISATION_LONG_NAME'].unique()) ^ set(R13_positive['ORGANISATION_LONG_NAME'].unique())

{'Commonwealth Scholarship Commission',
 'Independent Commission for Aid Impact'}

In [43]:

pd.options.display.max_columns = None

In [45]:
R13_positive[R13_positive['ORGANISATION_LONG_NAME']=='Independent Commission for Aid Impact']

YEAR_NO YEAR_SHORT_NAME QUARTER_SHORT_NAME MONTH_SHORT_NAME  \
1836520     2020         2020-21       Qtr3 - 20-21           Oct-20   
1836521     2020         2020-21       Qtr2 - 20-21           Sep-20   
1836522     2020         2020-21       Qtr3 - 20-21           Dec-20   
1836523     2020         2020-21       Qtr4 - 20-21           Feb-21   
1836524     2020         2020-21       Qtr3 - 20-21           Nov-20   
1836525     2020         2020-21       Qtr4 - 20-21           Jan-21   
1836526     2020         2020-21       Qtr2 - 20-21           Aug-20   
1836527     2020         2020-21       Qtr1 - 20-21           Jun-20   
1836528     2020         2020-21       Qtr2 - 20-21           Jul-20   
1836529     2020         2020-21       Qtr4 - 20-21           Mar-21   
1836530     2020         2020-21       Qtr1 - 20-21           May-20   
1836531     2020         2020-21       Qtr1 - 20-21           Apr-20   

        BUDGETING_ORGANISATIONS_CODE DEPARTMENT_GROUP_CODE  \
1836520                  DEPARTMENTS          DID030.GROUP   
1836521                  DEPARTMENTS          DID030.GROUP   
1836522                  DEPARTMENTS          DID030.GROUP   
1836523                  DEPARTMENTS          DID030.GROUP   
1836524                  DEPARTMENTS          DID030.GROUP   
1836525                  DEPARTMENTS          DID030.GROUP   
1836526                  DEPARTMENTS          DID030.GROUP   
1836527                  DEPARTMENTS          DID030.GROUP   
1836528                  DEPARTMENTS          DID030.GROUP   
1836529                  DEPARTMENTS          DID030.GROUP   
1836530                  DEPARTMENTS          DID030.GROUP   
1836531                  DEPARTMENTS          DID030.GROUP   

                           DEPARTMENT_GROUP_LONG_NAME ORGANISATION_CODE  \
1836520  Foreign, Commonwealth and Development Office            ICA030   
1836521  Foreign, Commonwealth and Development Office            ICA030   
1836522  Foreign, Commonwealth and Development Office            ICA030   
1836523  Foreign, Commonwealth and Development Office            ICA030   
1836524  Foreign, Commonwealth and Development Office            ICA030   
1836525  Foreign, Commonwealth and Development Office            ICA030   
1836526  Foreign, Commonwealth and Development Office            ICA030   
1836527  Foreign, Commonwealth and Development Office            ICA030   
1836528  Foreign, Commonwealth and Development Office            ICA030   
1836529  Foreign, Commonwealth and Development Office            ICA030   
1836530  Foreign, Commonwealth and Development Office            ICA030   
1836531  Foreign, Commonwealth and Development Office            ICA030   

                        ORGANISATION_LONG_NAME ORGANISATION_TYPE_CODE  \
1836520  Independent Commission for Aid Impact                     CG   
1836521  Independent Commission for Aid Impact                     CG   
1836522  Independent Commission for Aid Impact                     CG   
1836523  Independent Commission for Aid Impact                     CG   
1836524  Independent Commission for Aid Impact                     CG   
1836525  Independent Commission for Aid Impact                     CG   
1836526  Independent Commission for Aid Impact                     CG   
1836527  Independent Commission for Aid Impact                     CG   
1836528  Independent Commission for Aid Impact                     CG   
1836529  Independent Commission for Aid Impact                     CG   
1836530  Independent Commission for Aid Impact                     CG   
1836531  Independent Commission for Aid Impact                     CG   

        ORGANISATION_TYPE_LONG_NAME ORGANISATION_TYPE_L1_CODE  \
1836520          CENTRAL GOVERNMENT                       ALB   
1836521          CENTRAL GOVERNMENT                       ALB   
1836522          CENTRAL GOVERNMENT                       ALB   
1836523          CENTRAL GOVERNMENT                       ALB   
1836524       

In [37]:
oscar_grouped_df.to_excel('2022_11_15_oscar_grouped.xlsx')

In [ ]:
# want to add columns to the oscar dataset and add in information about the org status
# new columns of "ORGANISATION_CODE", Type_of_organisation", "Exact status", "ONS name"

In [21]:
len(checked_orgs)

281

In [3]:
# want a refined checked dataframe with only the above categories
# clean the checked dataframe

# have storage lists for putting clean information
org_code_all = []
checked_org_name_all = []
org_type_all = []
exact_status_all = []

# run through each row
for j in range(0, len(checked_orgs)):
    
    # for the organisation name
    if type(checked_orgs['ONS name (manual)'][j]) is str:
        # this looks for a replacement name if given
        checked_org_name = checked_orgs['ONS name (manual)'][j]
    elif type(checked_orgs['Check flag'][j]) is str:
        # this checks if there has been a check flag raised during manual tagging
        # will not look further for an org name
        # instead will say check
        checked_org_name = 'CHECK: ' + checked_orgs['ORGANISATION_LONG_NAME'][j]
    else:
        # the original name was correct
        checked_org_name = checked_orgs['ORGANISATION_LONG_NAME'][j]
        
    
    # for the other categories
    # all codes are given
    org_code = checked_orgs['ORGANISATION_CODE'][j]
    
    # org type
    if type(checked_orgs['Type_of_organisation'][j]) is str:
        org_type = checked_orgs['Type_of_organisation'][j]
    else:
        org_type = 'CHECK'
    
    # exact status
    if type(checked_orgs['Exact Status'][j]) is str:
        exact_status = checked_orgs['Exact Status'][j]
    else:
        exact_status = 'CHECK'
        
    # assemble the information
    org_code_all.append(org_code)
    checked_org_name_all.append(checked_org_name)
    org_type_all.append(org_type)
    exact_status_all.append(exact_status)
    
    
# pull into a single checked dataframe
checked_orgs_df = pd.DataFrame(zip(org_code_all, checked_org_name_all, org_type_all, exact_status_all),
                              columns=['Organisation_Code', 'Checked_Organisation_Name', 'IfG_Organisation_Type', 'IfG_Organisation_Status'])
        




String found
String found
String found
String found
String found
String found
String found
String found
String found
String found
Incomplete information
String found
Incomplete information
Incomplete information
Incomplete information
String found
Incomplete information
Incomplete information
Incomplete information
Incomplete information
Incomplete information
Incomplete information
String found
Incomplete information
String found
String found
String found
String found
Incomplete information
Incomplete information
String found
Incomplete information
String found
Incomplete information
Incomplete information
String found
Incomplete information
String found
String found
Incomplete information
Incomplete information
Incomplete information
Incomplete information
Incomplete information
Incomplete information
String found
Incomplete information
Incomplete information
Incomplete information
Incomplete information
Incomplete information
Incomplete information
Incomplete information
Incomplete 

In [82]:
# add flags into the OSCAR dataframe

chk_org_name = []
ifg_org_type = []
ifg_org_stat = []

for j in range(0, len(oscar)):
    
    org_code = oscar['ORGANISATION_CODE'][j]
    
    # check the name with the code only appears once...
    org_long_name = oscar['ORGANISATION_LONG_NAME'][j]
    
    if len(oscar[oscar['ORGANISATION_LONG_NAME']==org_long_name]['ORGANISATION_CODE'].unique()) == 1:
        # proceed as before
        chk_org_name.append(checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['Checked_Organisation_Name'].values[0])
        ifg_org_type.append(checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['IfG_Organisation_Type'].values[0])
        ifg_org_stat.append(checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['IfG_Organisation_Status'].values[0])
    
    elif len(oscar[oscar['ORGANISATION_LONG_NAME']==org_long_name]['ORGANISATION_CODE'].unique()) > 1:
        
        # if the current code matches, no need to panic
        if len(checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['Checked_Organisation_Name'].values) == 1:
            # as before
            chk_org_name.append(checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['Checked_Organisation_Name'].values[0])
            ifg_org_type.append(checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['IfG_Organisation_Type'].values[0])
            ifg_org_stat.append(checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['IfG_Organisation_Status'].values[0])
        elif len(checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['Checked_Organisation_Name'].values) == 0:
            # try the other code
            # match the codes
            # try the other code
            org_code_list = oscar[oscar['ORGANISATION_LONG_NAME']==org_long_name]['ORGANISATION_CODE'].unique().tolist()
            org_code_list.remove(org_code)
            if len(org_code_list) == 1:
                org_code = org_code_list[0]
            else:
                print('still too many organisations')
            chk_org_name.append(checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['Checked_Organisation_Name'].values[0])
            ifg_org_type.append(checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['IfG_Organisation_Type'].values[0])
            ifg_org_stat.append(checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['IfG_Organisation_Status'].values[0])
        else:
            print('struggling')
        
        
    elif len(oscar[oscar['ORGANISATION_LONG_NAME']==org_long_name]['ORGANISATION_CODE'].unique()) == 0:
        print('FUCK - no matches found')
        
        
    if (j/10000).is_integer is True:
        print(str(100*(j/len(oscar)))+' completed')
        
        
        
        
# add these to the OSCAR dataframe
oscar['Checked_Organisation_Name'] = chk_org_name
oscar['IfG_Organisation_Type'] = ifg_org_type
oscar['IfG_Organisation_Status'] = ifg_org_stat

KeyboardInterrupt: 

In [ ]:
(1.1).isinteger

In [83]:
j

1233207

In [25]:
checked_orgs_df

Organisation_Code                          Checked_Organisation_Name  \
0              TNA067                              The National Archives   
1              GAD031                    Government Actuary's Department   
2              CHC009           Charity Commission for England and Wales   
3              NSI049                                               NS&I   
4              DFE022                           Department for Education   
..                ...                                                ...   
276            MAC030              Marshall Aid Commemoration Commission   
277            LCR004             CHECK: London and Continental Railways   
278            FFL084                   CHECK: Fleetbank Funding Limited   
279            DPC032  Disabled People's Employment Corporation (GB) Ltd   
280            PSH084                Postal Services Holding Company plc   

    IfG_Organisation_Type                          IfG_Organisation_Status  
0             Public body                       Non-Ministerial Department  
1             Public body                       Non-Ministerial Department  
2             Public body                       Non-Ministerial Department  
3             Public body  Non-Ministerial Department and Executive Agency  
4              Department                                       Department  
..                    ...                                              ...  
276           Public Body                                   Executive NDPB  
277           Public Body                               Public Corporation  
278                 CHECK                                            CHECK  
279           Public Body                               Public Corporation  
280           Public Body                               Public Corporation  

[281 rows x 4 columns]

In [20]:
checked_orgs

ORGANISATION_CODE                             ORGANISATION_LONG_NAME  \
0              TNA067                              The National Archives   
1              GAD031                    Government Actuary's Department   
2              CHC009                                 Charity Commission   
3              NSI049                   National Savings and Investments   
4              DFE022                           Department for Education   
..                ...                                                ...   
276            MAC030              Marshall Aid Commemoration Commission   
277            LCR004                    London and Continental Railways   
278            FFL084                          Fleetbank Funding Limited   
279            DPC032  Disabled People's Employment Corporation (GB) Ltd   
280            PSH084                Postal Services Holding Company plc   

                                             ONS names  Match score  \
0                               National Archives, The          100   
1                      Government Actuary's Department          100   
2                                                 none           68   
3                 National Investment and Loans Office           76   
4                             Department for Education          100   
..                                                 ...          ...   
276              Marshall Aid Commemoration Commission          100   
277                                               none           51   
278                                               none           52   
279  Disabled People’s Employment Corporation (UK) Ltd           94   
280               Postal Services Holding Company Plc.          100   

                   Failed matched names  \
0                                   NaN   
1                                   NaN   
2               British Film Commission   
3                                   NaN   
4                                   NaN   
..                                  ...   
276                                 NaN   
277  Doctors’ and Dentists’ Review Body   
278               Bradford Film Limited   
279                                 NaN   
280                                 NaN   

                           Reasons for incorrect match Type_of_organisation  \
0                                                  NaN          Public body   
1                                                  NaN          Public body   
2    Listed in ONS dataset as "Charity Commission f...          Public body   
3                      Listed in ONS dataset as "NS&I"          Public body   
4                                                  NaN           Department   
..                                                 ...                  ...   
276                                                NaN          Public Body   
277                                                NaN          Public Body   
278                                                NaN                CHECK   
279                                                NaN          Public Body   
280                                                NaN          Public Body   

                                        Exact Status  \
0                         Non-Ministerial Department   
1                         Non-Ministerial Department   
2                         Non-Ministerial Department   
3    Non-Ministerial Department and Executive Agency   
4                                         Department   
..                                               ...   
276                                   Executive NDPB   
277                               Public Corporation   
278                                              NaN   
279                               Public Corporation   
280                               Public Corporation   

                            ONS name (manual)  \
0                                         NaN   
1

In [4]:
oscar_orgs = oscar[['ORGANISATION_LONG_NAME', 'ORGANISATION_CODE']] 

In [41]:
red_oscar_orgs = oscar_orgs.drop_duplicates(subset = 'ORGANISATION_LONG_NAME', keep='first')

In [42]:
red_oscar_orgs.reset_index(drop=True)

ORGANISATION_LONG_NAME ORGANISATION_CODE
0                                The National Archives            TNA067
1                      Government Actuary's Department            GAD031
2                                   Charity Commission            CHC009
3                     National Savings and Investments            NSI049
4                             Department for Education            DFE022
..                                                 ...               ...
276              Marshall Aid Commemoration Commission            MAC030
277                    London and Continental Railways            LCR004
278                          Fleetbank Funding Limited            FFL084
279  Disabled People's Employment Corporation (GB) Ltd            DPC032
280                Postal Services Holding Company plc            PSH084

[281 rows x 2 columns]

In [5]:
red_oscar_orgs

ORGANISATION_LONG_NAME ORGANISATION_CODE
0                                    The National Archives            TNA067
1                          Government Actuary's Department            GAD031
2                                       Charity Commission            CHC009
3                         National Savings and Investments            NSI049
4                                 Department for Education            DFE022
...                                                    ...               ...
34658                Marshall Aid Commemoration Commission            MAC030
299863                     London and Continental Railways            LCR004
591921                           Fleetbank Funding Limited            FFL084
1139777  Disabled People's Employment Corporation (GB) Ltd            DPC032
1773233                Postal Services Holding Company plc            PSH084

[281 rows x 2 columns]

In [ ]:
# now need to compare the two reduced (red_) organisation lists using thefuzz!

In [86]:
# 17-10-2022
#   To filter dataframe before matching organisations

# find the unique list of organisations from OSCAR (again)
org_long_name_list = oscar['ORGANISATION_LONG_NAME'].unique()

# for each segment/organisation, do something...
for j in range(0, len(org_long_name_list)):
    
    # take out the segment from oscar
    oscar_segment = oscar[oscar['ORGANISATION_LONG_NAME']==org_long_name_list[j]]
    # reset its index
    oscar_segment.reset_index(drop=True, inplace=True)

    # take the top code & long name
    org_long_name = org_long_name_list[j]
    org_code = oscar_segment['ORGANISATION_CODE'][0]
    
    # run a matching routine
    oscar_segment = organisation_matching(org_code, org_long_name, checked_orgs_df, oscar_segment)
    
    # pull out the values desired
    org_summary_df = summarise_org_spending(org_code, org_long_name, oscar_segment)
    
    # append the segments again for future reference
    if j == 0:
        new_oscar = oscar_segment
        summary_totals = org_summary_df
    else:
        new_oscar = pd.concat([new_oscar, oscar_segment], ignore_index=True)
        summary_totals = pd.concat([summary_totals, org_summary_df], ignore_index=True)

    print(j)
        

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try us

0
1


C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try us

2


C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try us

...

278


C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try us

279


C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\2388145651.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try us

280


In [35]:
# function to check orgs

def organisation_matching(org_code, org_long_name, checked_orgs_df, oscar_segment):

    chk_org_name = checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['Checked_Organisation_Name'].values[0]
    ifg_org_type = checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['IfG_Organisation_Type'].values[0]
    ifg_org_stat = checked_orgs_df[checked_orgs_df['Organisation_Code']==org_code]['IfG_Organisation_Status'].values[0]

    # add these to the OSCAR dataframe
    oscar_segment['Checked_Organisation_Name'] = chk_org_name
    oscar_segment['IfG_Organisation_Type'] = ifg_org_type
    oscar_segment['IfG_Organisation_Status'] = ifg_org_stat
    
    return oscar_segment

In [8]:
# function to get out the summary values

def summarise_org_spending(org_code, org_long_name, oscar_segment):
    
    # pull out the categories on the CONTROL_BUDGET_L0_LONG_NAME
    categories = oscar_segment.groupby('CONTROL_BUDGET_L0_LONG_NAME')['AMOUNT'].sum()
    
    # cast series to dataframe
    categories_df = categories.to_frame().T
    # reset index accordingly
    categories_df.reset_index(inplace=True, drop=True)    
    
    # add org information into it
    categories_df['Checked_Organisation_Name'] = oscar_segment['Checked_Organisation_Name'][0]
    categories_df['IfG_Organisation_Type'] = oscar_segment['IfG_Organisation_Type'][0]
    categories_df['IfG_Organisation_Status'] = oscar_segment['IfG_Organisation_Status'][0]
    
    return categories_df

In [93]:
def combine_and_summarise_org_spending(org_code, org_long_name, oscar_segment):
    
    # combine the CONTROL_BUDGET_L0_LONG_NAME and ECONOMIC_BUDGET_CODE
    
    for j in range(0, len(oscar_segment)):
        
        try:
            combined_cat = oscar_segment['ECONOMIC_BUDGET_CODE'][j] + " " + oscar_segment['CONTROL_BUDGET_L0_LONG_NAME'][j]
        except TypeError:
            combined_cat = str(oscar_segment['ECONOMIC_BUDGET_CODE'][j]) + " " + str(oscar_segment['CONTROL_BUDGET_L0_LONG_NAME'][j])

        
        if j == 0:
            combined_cat_list = [combined_cat]
        else:
            combined_cat_list.append(combined_cat)
            
    oscar_segment['Combined_IfG_Categories'] = combined_cat_list
    
    # pull out the categories on the combined category
    categories_all_values = oscar_segment.groupby('Combined_IfG_Categories')['AMOUNT'].sum()
    
    # sum non-negative values
    categories_positive = oscar_segment.groupby('Combined_IfG_Categories')['AMOUNT'].sum()
    
    # filter out the NON-BUDGET, NON-VOTED categories and sum
    categories_all_values_filter_budget = 
    
    # filter out the NON-BUDGET, NON-VOTED categories and sum positive values
    categories_positive_filter_budget = 
    
    # cast series to dataframe
    categories_df = categories.to_frame().T
    # reset index accordingly
    categories_df.reset_index(inplace=True, drop=True)    
    
    # add org information into it
    categories_df['Checked_Organisation_Name'] = oscar_segment['Checked_Organisation_Name'][0]
    categories_df['IfG_Organisation_Type'] = oscar_segment['IfG_Organisation_Type'][0]
    categories_df['IfG_Organisation_Status'] = oscar_segment['IfG_Organisation_Status'][0]
    
    return categories_df, oscar_segment
    

In [5]:
orr = R13_df[R13_df['Checked_Organisation_Name']=='Office of Rail Regulation']

In [9]:
orr['AMOUNT'].sum()

3297.0

In [8]:
orr[orr['AMOUNT']>0]['AMOUNT'].sum()

39925.0

In [40]:
orr[(orr['ECONOMIC_BUDGET_CODE'] == 'RESOURCE') & (orr['AMOUNT'] > 0)]['AMOUNT'].sum()

36700.0

In [25]:
orr.groupby('ECONOMIC_BUDGET_CODE')['AMOUNT'].sum().apply(lambda x: x if (x > 0) else 0)

ECONOMIC_BUDGET_CODE
CAPITAL     720.0
RESOURCE     72.0
Name: AMOUNT, dtype: float64

In [94]:
#   To filter dataframe after matching organisations

# find the unique list of organisations from new_oscar
org_long_name_list = new_oscar['ORGANISATION_LONG_NAME'].unique()

# for each segment/organisation, do something...
for j in range(0, len(org_long_name_list)):
    
    # take out the segment from oscar
    oscar_segment = new_oscar[new_oscar['ORGANISATION_LONG_NAME']==org_long_name_list[j]]
    # reset its index
    oscar_segment.reset_index(drop=True, inplace=True)

    # take the top code & long name
    org_long_name = org_long_name_list[j]
    org_code = oscar_segment['ORGANISATION_CODE'][0]
    
    # pull out the categories
    comb_org_summary_df, comb_oscar_summary = combine_and_summarise_org_spending(org_code, org_long_name, oscar_segment)
    
    # append the segments again for future reference
    if j == 0:
        comb_summary_totals = comb_org_summary_df
        comb_oscar_summary_all = comb_oscar_summary
    else:
        comb_summary_totals = pd.concat([comb_summary_totals, comb_org_summary_df], ignore_index=True)
        comb_oscar_summary_all = pd.concat([comb_oscar_summary_all, comb_oscar_summary], ignore_index=True)
    print(j)
        

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\425204731.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\425204731.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list


0


C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\425204731.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list


1
2
3


C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\425204731.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\425204731.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list


...

278


C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\425204731.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list


279


C:\Users\shepleyp\AppData\Local\Temp\ipykernel_6140\425204731.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list


280


In [96]:
# pickle up the dataframes!

new_oscar.to_pickle('2022_10_17_matched_oscar.pkl')
summary_totals.to_pickle('2022_10_17_summary_L0_orgs.pkl')


In [98]:
comb_summary_totals.to_pickle('2022_10_17_combined_summaries_orgs.pkl')
comb_oscar_summary_all.to_pickle('2022_10_17_comb_matched_oscar.pkl')

In [102]:
# save up the summaries in an excel sheet

with pd.ExcelWriter('oscar_summaries.xlsx') as writer:
    
    summary_totals.to_excel(writer, sheet_name='L0_summary')
    comb_summary_totals.to_excel(writer, sheet_name='comb_cat_summary')



In [87]:
summary_totals

CONTROL_BUDGET_L0_LONG_NAME  ANNUALLY MANAGED EXPENDITURE  \
0                                                    35.0   
1                                                   130.0   
2                                                   200.0   
3                                                 42900.0   
4                                             302134912.0   
..                                                    ...   
276                                                   NaN   
277                                                   0.0   
278                                              -11574.0   
279                                                   NaN   
280                                                   NaN   

CONTROL_BUDGET_L0_LONG_NAME  DEPARTMENTAL EXPENDITURE LIMITS  NON-BUDGET  \
0                                               5.652680e+05     34581.0   
1                                               1.026000e+03      4309.0   
2                                               4.703670e+05     23832.0   
3                                               2.214182e+06    534122.0   
4                                               1.203878e+09  86282156.0   
..                                                       ...         ...   
276                                             2.480000e+03      2700.0   
277                                                      NaN         NaN   
278                                             7.455300e+04         NaN   
279                                                      NaN     39387.0   
280                                             2.000000e+00         NaN   

CONTROL_BUDGET_L0_LONG_NAME                          Checked_Organisation_Name  \
0                                                        The National Archives   
1                                              Government Actuary's Department   
2                                     Charity Commission for England and Wales   
3                                                                         NS&I   
4                                                     Department for Education   
..                                                                         ...   
276                                      Marshall Aid Commemoration Commission   
277                                     CHECK: London and Continental Railways   
278                                           CHECK: Fleetbank Funding Limited   
279                          Disabled People's Employment Corporation (GB) Ltd   
280                                        Postal Services Holding Company plc   

CONTROL_BUDGET_L0_LONG_NAME IfG_Organisation_Type  \
0                                     Public body   
1                                     Public body   
2                                     Public body   
3                                     Public body   
4                                      Department   
..                                            ...   
276                                   Public Body   
277                                   Public Body   
278                                         CHECK   
279                                   Public Body   
280                                   Public Body   

CONTROL_BUDGET_L0_LONG_NAME                          IfG_Organisation_Status  
0                                                 Non-Ministerial Department  
1                                                 Non-Ministerial Department  
2                                                 Non-Ministerial Department  
3                            Non-Ministerial Department and Executive Agency  
4                                                                 Department  
..                                                                       ...  
276                                                           Executive NDPB  
277                                                       Public Corporation  
278                  

In [ ]:
# 2022-10-25 work starts here
# uses the already matched and pickled OSCAR data
# 

In [2]:
# load pickled matched data

new_oscar = pd.read_pickle('2022_10_17_matched_oscar.pkl')



In [3]:
# extract the R13 version data

R13_df = new_oscar[new_oscar['VERSION_CODE']=='R13']

In [4]:
orr = R13_df[R13_df['Checked_Organisation_Name']=='Office of Rail Regulation']

In [24]:
R13_df['AMOUNT'].sum()

1394189186.0

In [11]:
orr['AMOUNT'].unique()

array([ 6.000e+01, -1.305e+03, -1.530e+03, -1.535e+03, -1.304e+03,
       -3.000e+00, -7.000e+00, -1.000e+00, -2.100e+02, -2.150e+02,
        6.000e+00,  7.000e+00,  8.000e+00,  1.000e+00,  1.000e+01,
        9.000e+00,  9.330e+02,  9.360e+02,  1.097e+03,  1.102e+03,
        1.100e+02,  1.110e+02,  2.700e+02,  2.640e+02,  3.200e+02,
        8.400e+01,  8.000e+01,  3.500e+01,  3.400e+01,  4.100e+01,
        6.600e+01,  6.300e+01,  5.600e+01,  5.700e+01,  2.090e+02,
        2.060e+02,  3.000e+00,  2.000e+00, -4.000e+00])

In [5]:
orr[orr['AMOUNT']>0]['AMOUNT'].sum()

39925.0

In [14]:
orr2 = orr.groupby(['PESA_ECONOMIC_BUDGET_CODE','PESA_ECONOMIC_GROUP_CODE','INCOME_CATEGORY_SHORT_NAME','CHART_OF_ACCOUNTS_L5_LONG_NAME'])['AMOUNT'].sum()

In [17]:
orr2

PESA_ECONOMIC_BUDGET_CODE  PESA_ECONOMIC_GROUP_CODE                           INCOME_CATEGORY_SHORT_NAME  CHART_OF_ACCOUNTS_L5_LONG_NAME                                  
CAPITAL                    PURCHASE OF ASSETS                                 GROSS                       PPE - BUILDINGS (OWNED) - COST - ADDITIONS                            720.0
RESOURCE                   DEPRECIATION                                       GROSS                       EXP - AMORTISATION - INTANGIBLE ASSETS                                169.0
                                                                                                          EXP - DEPRECIATION - PPE (OWNED)                                      978.0
                           OTHER RESOURCE                                     GROSS                       EXP - NOTIONAL AUDITORS REMUNERATION AND EXPENSES                      51.0
                                                                              OTHER INCOME           

In [9]:
display(orr)

YEAR_NO YEAR_SHORT_NAME QUARTER_SHORT_NAME MONTH_SHORT_NAME  \
304933     2020         2020-21       Qtr4 - 20-21           Feb-21   
304934     2020         2020-21       Qtr2 - 20-21           Jul-20   
304935     2020         2020-21       Qtr2 - 20-21           Sep-20   
304936     2020         2020-21       Qtr3 - 20-21           Nov-20   
304937     2020         2020-21       Qtr1 - 20-21           May-20   
...         ...             ...                ...              ...   
305244     2020         2020-21       Qtr3 - 20-21           Oct-20   
305245     2020         2020-21       Qtr3 - 20-21           Dec-20   
305246     2020         2020-21       Qtr3 - 20-21           Nov-20   
305247     2020         2020-21       Qtr4 - 20-21           Jan-21   
305248     2020         2020-21       Qtr2 - 20-21           Jul-20   

       BUDGETING_ORGANISATIONS_CODE DEPARTMENT_GROUP_CODE  \
304933                  DEPARTMENTS          ORR088.GROUP   
304934                  DEPARTMENTS          ORR088.GROUP   
304935                  DEPARTMENTS          ORR088.GROUP   
304936                  DEPARTMENTS          ORR088.GROUP   
304937                  DEPARTMENTS          ORR088.GROUP   
...                             ...                   ...   
305244                  DEPARTMENTS          ORR088.GROUP   
305245                  DEPARTMENTS          ORR088.GROUP   
305246                  DEPARTMENTS          ORR088.GROUP   
305247                  DEPARTMENTS          ORR088.GROUP   
305248                  DEPARTMENTS          ORR088.GROUP   

       DEPARTMENT_GROUP_LONG_NAME ORGANISATION_CODE  \
304933    Office of Rail and Road            ORR088   
304934    Office of Rail and Road            ORR088   
304935    Office of Rail and Road            ORR088   
304936    Office of Rail and Road            ORR088   
304937    Office of Rail and Road            ORR088   
...                           ...               ...   
305244    Office of Rail and Road            ORR088   
305245    Office of Rail and Road            ORR088   
305246    Office of Rail and Road            ORR088   
305247    Office of Rail and Road            ORR088   
305248    Office of Rail and Road            ORR088   

           ORGANISATION_LONG_NAME ORGANISATION_TYPE_CODE  ... VERSION_CODE  \
304933  Office of Rail Regulation                     CG  ...          R13   
304934  Office of Rail Regulation                     CG  ...          R13   
304935  Office of Rail Regulation                     CG  ...          R13   
304936  Office of Rail Regulation                     CG  ...          R13   
304937  Office of Rail Regulation                     CG  ...          R13   
...                           ...                    ...  ...          ...   
305244  Office of Rail Regulation                     CG  ...          R13   
305245  Office of Rail Regulation                     CG  ...          R13   
305246  Office of Rail Regulation                     CG  ...          R13   
305247  Office of Rail Regulation                     CG  ...          R13   
305248  Office of Rail Regulation                     CG  ...          R13   

       FCT_LOAD_TYPE_CODE       FCT_LOAD_TYPE_LONG_NAME ROW_DESCRIPTION  \
304933           EP_APP8_  COGNOS EP Forecast Outturn A                   
304934           EP_APP8_  COGNOS EP Forecast Outturn A                   
304935           EP_APP8_  COGNOS EP Forecast Outturn A                   
304936           EP_APP8_  COGNOS EP Forecast Outturn A                   
304937           EP_APP8_  COGNOS EP Forecast Outturn A                   
...                   ...                           ...             ...   
305244           EP_APP8_  COGNOS EP Forecast Outturn A                   
305245           EP_APP8_  COGNOS EP Forecast Outturn A                   
305246           EP_APP8_  COGNOS EP Forecast Outturn A                   
305247           EP_APP8_  COGNOS EP Forecast Outturn A                   

In [13]:
orr.to_excel('orr_snapshot.xlsx')

In [19]:
# quick extraction for checking
orr = R13_df[R13_df['Checked_Organisation_Name']=='Office of Rail Regulation']
dvta = R13_df[R13_df['Checked_Organisation_Name']=='Driver and Vehicle Testing Agency']
bfi = R13_df[R13_df['Checked_Organisation_Name']=='British Film Institute']
ncs = R13_df[R13_df['Checked_Organisation_Name']=='National Citizen Service']
nhm = R13_df[R13_df['Checked_Organisation_Name']=='Natural History Museum']


In [ ]:

with pd.ExcelWriter('oscar_summaries_for_checking.xlsx') as writer:
    
    orr.to_excel(writer, sheet_name='Office of Rail Regulation')
    dvta.to_excel(writer, sheet_name='Driver and Vehicle Testing')
    bfi.to_excel(writer, sheet_name='British Film Institute')
    ncs.to_excel(writer, sheet_name='National Citizen Service')
    nhm.to_excel(writer, sheet_name='Natural History Museum')
    org_long_name.to_excel(writer, sheet_name='ORGANISATION_LONG_NAME')

In [25]:
# collate the categories
orr2 = orr.groupby(['PESA_ECONOMIC_BUDGET_CODE','PESA_ECONOMIC_GROUP_CODE','INCOME_CATEGORY_SHORT_NAME','CHART_OF_ACCOUNTS_L5_LONG_NAME', 'CONTROL_BUDGET_L0_LONG_NAME','ACCOUNTING_AUTHORITY_L0_CODE'])['AMOUNT'].sum()
dvta2 = dvta.groupby(['PESA_ECONOMIC_BUDGET_CODE','PESA_ECONOMIC_GROUP_CODE','INCOME_CATEGORY_SHORT_NAME','CHART_OF_ACCOUNTS_L5_LONG_NAME', 'CONTROL_BUDGET_L0_LONG_NAME','ACCOUNTING_AUTHORITY_L0_CODE'])['AMOUNT'].sum()
bfi2 = bfi.groupby(['PESA_ECONOMIC_BUDGET_CODE','PESA_ECONOMIC_GROUP_CODE','INCOME_CATEGORY_SHORT_NAME','CHART_OF_ACCOUNTS_L5_LONG_NAME', 'CONTROL_BUDGET_L0_LONG_NAME','ACCOUNTING_AUTHORITY_L0_CODE'])['AMOUNT'].sum()
ncs2 = ncs.groupby(['PESA_ECONOMIC_BUDGET_CODE','PESA_ECONOMIC_GROUP_CODE','INCOME_CATEGORY_SHORT_NAME','CHART_OF_ACCOUNTS_L5_LONG_NAME', 'CONTROL_BUDGET_L0_LONG_NAME','ACCOUNTING_AUTHORITY_L0_CODE'])['AMOUNT'].sum()
nhm2 = nhm.groupby(['PESA_ECONOMIC_BUDGET_CODE','PESA_ECONOMIC_GROUP_CODE','INCOME_CATEGORY_SHORT_NAME','CHART_OF_ACCOUNTS_L5_LONG_NAME', 'CONTROL_BUDGET_L0_LONG_NAME','ACCOUNTING_AUTHORITY_L0_CODE'])['AMOUNT'].sum()

In [26]:

with pd.ExcelWriter('collated_oscar_summaries_for_checking.xlsx') as writer:
    
    orr2.to_excel(writer, sheet_name='Office of Rail Regulation')
    dvta2.to_excel(writer, sheet_name='Driver and Vehicle Testing')
    bfi2.to_excel(writer, sheet_name='British Film Institute')
    ncs2.to_excel(writer, sheet_name='National Citizen Service')
    nhm2.to_excel(writer, sheet_name='Natural History Museum')
    org_long_name.to_excel(writer, sheet_name='ORGANISATION_LONG_NAME')


In [28]:
ncs

YEAR_NO YEAR_SHORT_NAME QUARTER_SHORT_NAME MONTH_SHORT_NAME  \
1451088     2020         2020-21       Qtr4 - 20-21           Mar-21   
1451089     2020         2020-21       Qtr4 - 20-21           Feb-21   
1451090     2020         2020-21       Qtr3 - 20-21           Nov-20   
1451091     2020         2020-21       Qtr2 - 20-21           Sep-20   
1451092     2020         2020-21       Qtr1 - 20-21           May-20   
...          ...             ...                ...              ...   
1451165     2020         2020-21       Qtr3 - 20-21           Oct-20   
1451166     2020         2020-21       Qtr4 - 20-21           Feb-21   
1451167     2020         2020-21       Qtr1 - 20-21           Jun-20   
1451168     2020         2020-21       Qtr4 - 20-21           Jan-21   
1451169     2020         2020-21       Qtr2 - 20-21           Jul-20   

        BUDGETING_ORGANISATIONS_CODE DEPARTMENT_GROUP_CODE  \
1451088                  DEPARTMENTS          DCM048.GROUP   
1451089                  DEPARTMENTS          DCM048.GROUP   
1451090                  DEPARTMENTS          DCM048.GROUP   
1451091                  DEPARTMENTS          DCM048.GROUP   
1451092                  DEPARTMENTS          DCM048.GROUP   
...                              ...                   ...   
1451165                  DEPARTMENTS          DCM048.GROUP   
1451166                  DEPARTMENTS          DCM048.GROUP   
1451167                  DEPARTMENTS          DCM048.GROUP   
1451168                  DEPARTMENTS          DCM048.GROUP   
1451169                  DEPARTMENTS          DCM048.GROUP   

                               DEPARTMENT_GROUP_LONG_NAME ORGANISATION_CODE  \
1451088  Department for Digital, Culture, Media and Sport            NCS048   
1451089  Department for Digital, Culture, Media and Sport            NCS048   
1451090  Department for Digital, Culture, Media and Sport            NCS048   
1451091  Department for Digital, Culture, Media and Sport            NCS048   
1451092  Department for Digital, Culture, Media and Sport            NCS048   
...                                                   ...               ...   
1451165  Department for Digital, Culture, Media and Sport            NCS048   
1451166  Department for Digital, Culture, Media and Sport            NCS048   
1451167  Department for Digital, Culture, Media and Sport            NCS048   
1451168  Department for Digital, Culture, Media and Sport            NCS048   
1451169  Department for Digital, Culture, Media and Sport            NCS048   

           ORGANISATION_LONG_NAME ORGANISATION_TYPE_CODE  ... VERSION_CODE  \
1451088  National Citizen Service                     CG  ...          R13   
1451089  National Citizen Service                     CG  ...          R13   
1451090  National Citizen Service                     CG  ...          R13   
1451091  National Citizen Service                     CG  ...          R13   
1451092  National Citizen Service                     CG  ...          R13   
...                           ...                    ...  ...          ...   
1451165  National Citizen Service                     CG  ...          R13   
1451166  National Citizen Service                     CG  ...          R13   
1451167  National Citizen Service                     CG  ...          R13   
1451168  National Citizen Service                     CG  ...          R13   
1451169  National Citizen Service                     CG  ...          R13   

        FCT_LOAD_TYPE_CODE       FCT_LOAD_TYPE_LONG_NAME ROW_DESCRIPTION  \
1451088           EP_APP8_  COGNOS EP Forecast Outturn A                   
1451089           EP_APP8_  COGNOS EP Forecast Outturn A                   
1451090           EP_APP8_  COGNOS EP Forecast Outturn A                   
1451091           EP_APP8_  COGNOS EP Forecast Outturn A                   
1451092           EP_APP8_  COGNOS EP Forecast Outturn A                   
...                    ...                           ... 

In [22]:
listing = R13_df['ORGANISATION_LONG_NAME'].unique()
org_long_name = pd.DataFrame(listing)

In [21]:
R13_df[R13_df['ORGANISATION_LONG_NAME'] .str.contains('FCA')]['ORGANISATION_LONG_NAME'].unique()

array([], dtype=object)

In [ ]:
df[df['ids'].str.contains("ball")]

In [27]:
org_long_name

0
0                    The National Archives
1          Government Actuary's Department
2                       Charity Commission
3         National Savings and Investments
4                 Department for Education
..                                     ...
246             Great Britain China Centre
247  Marshall Aid Commemoration Commission
248        London and Continental Railways
249              Fleetbank Funding Limited
250    Postal Services Holding Company plc

[251 rows x 1 columns]

In [5]:
# sum of annual spending

R13_df['AMOUNT'].sum()

1394189186.0

In [7]:
# check it's for one financial year

R13_df['YEAR_SHORT_NAME'].unique()

array(['2020-21'], dtype=object)

In [13]:
# find the unique list of organisations from OSCAR (again)
org_long_name_list = R13_df['ORGANISATION_LONG_NAME'].unique()

# for each segment/organisation, do something...
for j in range(0, len(org_long_name_list)):
    
    # take out the segment from the selected part of the data
    oscar_segment = R13_df[R13_df['ORGANISATION_LONG_NAME']==org_long_name_list[j]]
    # reset its index
    oscar_segment.reset_index(drop=True, inplace=True)

    # take the top code & long name
    org_long_name = org_long_name_list[j]
    org_code = oscar_segment['ORGANISATION_CODE'][0]
    
    # pull out the values desired
    # take the spending summary based on prior values
    org_summary_df = summarise_org_spending(org_code, org_long_name, oscar_segment)
    # make a cut using the combined categories
    comb_org_summary_df, comb_oscar_summary = combine_and_summarise_org_spending(org_code, org_long_name, oscar_segment)
    
    # append the segments again for future reference
    if j == 0:
        summary_totals = org_summary_df
        comb_summary_totals = comb_org_summary_df
        comb_oscar_summary_all = comb_oscar_summary
    else:
        summary_totals = pd.concat([summary_totals, org_summary_df], ignore_index=True)
        comb_summary_totals = pd.concat([comb_summary_totals, comb_org_summary_df], ignore_index=True)
        comb_oscar_summary_all = pd.concat([comb_oscar_summary_all, comb_oscar_summary], ignore_index=True)

with pd.ExcelWriter('oscar_summaries_2.xlsx') as writer:
    
    summary_totals.to_excel(writer, sheet_name='L0_summary')
    comb_summary_totals.to_excel(writer, sheet_name='comb_cat_summary')
        

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

...

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Combined_IfG_Categories'] = combined_cat_list
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_18764\1784544393.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

In [9]:
# function to get out the summary values

def summarise_org_spending(org_code, org_long_name, oscar_segment):
    
    # pull out the categories on the CONTROL_BUDGET_L0_LONG_NAME
    categories = oscar_segment.groupby('CONTROL_BUDGET_L0_LONG_NAME')['AMOUNT'].sum()
    
    # cast series to dataframe
    categories_df = categories.to_frame().T
    # reset index accordingly
    categories_df.reset_index(inplace=True, drop=True)    
    
    # add org information into it
    categories_df['Checked_Organisation_Name'] = oscar_segment['Checked_Organisation_Name'][0]
    categories_df['IfG_Organisation_Type'] = oscar_segment['IfG_Organisation_Type'][0]
    categories_df['IfG_Organisation_Status'] = oscar_segment['IfG_Organisation_Status'][0]
    
    return categories_df

In [12]:
def combine_and_summarise_org_spending(org_code, org_long_name, oscar_segment):
    
    # combine the CONTROL_BUDGET_L0_LONG_NAME and ECONOMIC_BUDGET_CODE
    
    for j in range(0, len(oscar_segment)):
        
        try:
            combined_cat = oscar_segment['ECONOMIC_BUDGET_CODE'][j] + " " + oscar_segment['CONTROL_BUDGET_L0_LONG_NAME'][j]
        except TypeError:
            combined_cat = str(oscar_segment['ECONOMIC_BUDGET_CODE'][j]) + " " + str(oscar_segment['CONTROL_BUDGET_L0_LONG_NAME'][j])
        
        if j == 0:
            combined_cat_list = [combined_cat]
        else:
            combined_cat_list.append(combined_cat)
            
    oscar_segment['Combined_IfG_Categories'] = combined_cat_list
    
    # pull out the categories on the combined category
    categories = oscar_segment.groupby('Combined_IfG_Categories')['AMOUNT'].sum()
    
    # cast series to dataframe
    categories_df = categories.to_frame().T
    # reset index accordingly
    categories_df.reset_index(inplace=True, drop=True)    
    
    # add org information into it
    categories_df['Checked_Organisation_Name'] = oscar_segment['Checked_Organisation_Name'][0]
    categories_df['IfG_Organisation_Type'] = oscar_segment['IfG_Organisation_Type'][0]
    categories_df['IfG_Organisation_Status'] = oscar_segment['IfG_Organisation_Status'][0]
    
    return categories_df, oscar_segment

In [16]:
pd.set_option('display.max_rows', None)

In [6]:
R13_df

YEAR_NO YEAR_SHORT_NAME QUARTER_SHORT_NAME MONTH_SHORT_NAME  \
6878        2020         2020-21       Qtr2 - 20-21           Sep-20   
6879        2020         2020-21       Qtr1 - 20-21           Jun-20   
6880        2020         2020-21       Qtr4 - 20-21           Feb-21   
6881        2020         2020-21       Qtr4 - 20-21           Feb-21   
6882        2020         2020-21       Qtr4 - 20-21           Jan-21   
...          ...             ...                ...              ...   
1845459     2020         2020-21       Qtr4 - 20-21           Mar-21   
1845460     2020         2020-21       Qtr4 - 20-21           Mar-21   
1845461     2020         2020-21       Qtr4 - 20-21           Mar-21   
1845462     2020         2020-21       Qtr4 - 20-21           Mar-21   
1845468     2020         2020-21       Qtr4 - 20-21           Mar-21   

        BUDGETING_ORGANISATIONS_CODE DEPARTMENT_GROUP_CODE  \
6878                     DEPARTMENTS          TNA067.GROUP   
6879                     DEPARTMENTS          TNA067.GROUP   
6880                     DEPARTMENTS          TNA067.GROUP   
6881                     DEPARTMENTS          TNA067.GROUP   
6882                     DEPARTMENTS          TNA067.GROUP   
...                              ...                   ...   
1845459                  DEPARTMENTS          BIS084.GROUP   
1845460                  DEPARTMENTS          BIS084.GROUP   
1845461                  DEPARTMENTS          BIS084.GROUP   
1845462                  DEPARTMENTS          BIS084.GROUP   
1845468                  DEPARTMENTS          BIS084.GROUP   

                                DEPARTMENT_GROUP_LONG_NAME ORGANISATION_CODE  \
6878                                 The National Archives            TNA067   
6879                                 The National Archives            TNA067   
6880                                 The National Archives            TNA067   
6881                                 The National Archives            TNA067   
6882                                 The National Archives            TNA067   
...                                                    ...               ...   
1845459  Department for Business, Energy and Industrial...            FFL084   
1845460  Department for Business, Energy and Industrial...            FFL084   
1845461  Department for Business, Energy and Industrial...            FFL084   
1845462  Department for Business, Energy and Industrial...            FFL084   
1845468  Department for Business, Energy and Industrial...            PSH084   

                      ORGANISATION_LONG_NAME ORGANISATION_TYPE_CODE  ...  \
6878                   The National Archives                     CG  ...   
6879                   The National Archives                     CG  ...   
6880                   The National Archives                     CG  ...   
6881                   The National Archives                     CG  ...   
6882                   The National Archives                     CG  ...   
...                                      ...                    ...  ...   
1845459            Fleetbank Funding Limited                     CG  ...   
1845460            Fleetbank Funding Limited                     CG  ...   
1845461            Fleetbank Funding Limited                     CG  ...   
1845462            Fleetbank Funding Limited                     CG  ...   
1845468  Postal Services Holding Company plc                     CG  ...   

        VERSION_CODE FCT_LOAD_TYPE_CODE       FCT_LOAD_TYPE_LONG_NAME  \
6878             R13           EP_APP8_  COGNOS EP Forecast Outturn A   
6879             R13           EP_APP8_  COGNOS EP Forecast Outturn A   
6880             R13           EP_APP8_  COGNOS EP Forecast Outturn A   
6881             R13           EP_APP8_  COGNOS EP Forecast Outturn A   
6882             R13           EP_APP8_  COGNOS EP Forecast Outturn A   
...              ...                ...                           ...   
1845459       

In [18]:
new_oscar[new_oscar['Checked_Organisation_Name']=='NS&I']

YEAR_NO YEAR_SHORT_NAME QUARTER_SHORT_NAME  MONTH_SHORT_NAME  \
10068     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10069     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10070     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10071     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10072     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10073     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10074     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10075     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10076     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10077     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10078     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10079     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10080     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10081     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10082     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10083     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10084     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10085     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10086     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10087     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10088     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10089     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10090     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10091     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10092     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10093     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10094     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10095     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10096     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10097     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10098     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10099     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10100     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10101     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10102     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10103     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10104     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10105     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10106     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10107     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10108     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10109     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10110     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10111     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10112     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10113     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10114     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10115     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10116     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10117     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10118     2020         2020-21   Period 0 - 20-21  Period 0 - 20-21   
10119     2020         2020-21       Qtr4 - 20-21            Feb-21   
10120     2020         2020-21       Qtr4 - 20-21            Jan-21   
10121     2020         2020-21       Qtr3 - 20-21            Dec-20   
10122     2020         2020-21       Qtr3 - 20-21            Nov-20   
10123     2020         2020-21 

In [10]:
oscar['CONTROL_BUDGET_L0_LONG_NAME'].unique()

array(['DEPARTMENTAL EXPENDITURE LIMITS', 'ANNUALLY MANAGED EXPENDITURE',
       'NON-BUDGET'], dtype=object)

In [11]:
oscar['CONTROL_BUDGET_L1_LONG_NAME'].unique()

array(['DEPARTMENTAL EXPENDITURE LIMITS PROGRAMME',
       'DEPARTMENTAL EXPENDITURE LIMITS ADMINISTRATION',
       'DEPARTMENTAL ANNUALLY MANAGED EXPENDITURE', 'NON-BUDGET (NB)',
       'NON-DEPARTMENTAL ANNUALLY MANAGED EXPENDITURE'], dtype=object)

In [20]:
oscar.columns

Index(['YEAR_NO', 'YEAR_SHORT_NAME', 'QUARTER_SHORT_NAME', 'MONTH_SHORT_NAME',
       'BUDGETING_ORGANISATIONS_CODE', 'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_CODE',
       'ORGANISATION_TYPE_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE',
       'ORGANISATION_TYPE_L1_LONG_NAME', 'PESA_GROUP_CODE',
       'PESA_GROUP_LONG_NAME', 'SR_GROUP_CODE', 'SR_GROUP_LONG_NAME',
       'BX_VALIDATION_GROUP_CODE', 'BX_VALIDATION_GROUP_LONG_NAME',
       'FO_VALIDATION_GROUP_CODE', 'FO_VALIDATION_GROUP_LONG_NAME',
       'ACCOUNTING_ARRANGEMENTS_CODE', 'ACCOUNTING_ARRANGEMENTS_LONG_NAME',
       'COUNTER_ORGANISATION_CODE', 'COUNTER_ORGANISATION_LONG_NAME',
       'SEGMENT_L4_CODE', 'SEGMENT_L4_LONG_NAME', 'COFOG_L0_CODE',
       'COFOG_L0_LONG_NAME', 'COFOG_L1_CODE', 'COFOG_L1_LONG_NAME',
       'COFOG_L2_CODE', 'COFOG_L2_LONG_NAME', 'CONTROL_BUDGET_L0_LONG_NAME',
       'CONTROL_BUDGET_L1_LONG_NAME', 'COVERAGE_L

In [4]:
# build out a sample of the OSCAR dataset

# find number of unique values per category, print up to 10

list_of_cat_lists = []

for j in range(0, len(oscar.columns)):
    
    if len(oscar[oscar.columns[j]].unique()) <= 10:
        
        cat_list = oscar[oscar.columns[j]].unique()
        
    else:
        
        cat_list = oscar[oscar.columns[j]].unique()[:10]


    list_of_cat_lists.append(cat_list)


In [ ]:
# Save up the sample category information

In [8]:
workbook = xlsxwriter.Workbook('oscar_category_snapshot.xlsx')
worksheet = workbook.add_worksheet()

In [24]:
# write column names and unique value sets
for j in range(0, len(oscar.columns)):
    
    # write category list
    worksheet.write(j+1, 0, oscar.columns[j])
    
    # write the different unique values
    for k in range(0, len(list_of_cat_lists[j])):
        
        if type(list_of_cat_lists[j][k]) is not str:
            if np.isnan(list_of_cat_lists[j][k]):
                worksheet.write(j+1, 1+k, 'nan')
            else:
                worksheet.write(j+1, 1+k, list_of_cat_lists[j][k])
        else:
            worksheet.write(j+1, 1+k, list_of_cat_lists[j][k])
        
    # if more than 10 values, then add elipsis at the end
    if len(list_of_cat_lists[j]) == 10:
        
        worksheet.write(j+1, 1+11, '...')
    
# add titles
worksheet.write(0, 0, 'OSCAR CATEGORIES')
worksheet.write(0, 1, 'Sample values from OSCAR')
    

0

In [25]:
workbook.close()